In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datasets import load_from_disk
from transformers import AutoTokenizer

import json
import os
from datasets import Dataset

In [ ]:
# 시각화 스타일 설정
plt.style.use('seaborn-v0_8')
plt.rc('font', family='NanumBarunGothic') # 한글 폰트 설정 (환경에 맞게 변경)
plt.rcParams['axes.unicode_minus'] = False

In [ ]:
data_path = "../raw/data/"

train_path = "train_dataset/train/dataset.arrow"
test_path = "test_dataset/validation/dataset.arrow"
docs_path = "wikipedia_documents.json"


# 단일 arrow 파일 로드
train_df = Dataset.from_file(os.path.join(data_path, train_path))
test_df = Dataset.from_file(os.path.join(data_path, test_path))

# Pandas DataFrame으로 변환
train_df = train_df.to_pandas()
test_df = test_df.to_pandas()

In [ ]:
print(f"Train Size: {len(train_df)}")
print(f"Test Size: {len(test_df)}")

In [ ]:
def process_answers(row):
    if 'answers' in row and row['answers']:
        # Arrow 데이터셋 로드 시 딕셔너리 구조가 유지되는 경우와 그렇지 않은 경우 처리
        ans = row['answers']
        text = ans['text'][0] if len(ans['text']) > 0 else ""
        start = ans['answer_start'][0] if len(ans['answer_start']) > 0 else 0
        return text, start
    return None, None

# Train 데이터에만 정답 컬럼 생성
train_df[['answer_text', 'answer_start']] = train_df.apply(process_answers, axis=1, result_type='expand')

In [ ]:
model_name = "klue/roberta-large"
tokenizer = AutoTokenizer.from_pretrained(model_name)

print("\n토큰화 진행 중...")
train_df['q_len'] = train_df['question'].apply(lambda x: len(tokenizer.encode(x)))
test_df['q_len'] = test_df['question'].apply(lambda x: len(tokenizer.encode(x)))

plt.figure(figsize=(12, 6))
sns.kdeplot(train_df['q_len'], fill=True, label='Train Question', color='blue', alpha=0.3)
sns.kdeplot(test_df['q_len'], fill=True, label='Test Question', color='red', alpha=0.3)
plt.title("질문 토큰 길이 분포 비교 (Train vs Test)")
plt.xlabel("Token Count")
plt.legend()
plt.show()

print(f"Train Question Mean Length: {train_df['q_len'].mean():.2f}")
print(f"Test Question Mean Length:  {test_df['q_len'].mean():.2f}")

In [ ]:
def check_question_type(text):
    if any(x in text for x in ['누구', '인물', '사람', '배우', '작가', '대상']):
        return 'PERSON (인물)'
    elif any(x in text for x in ['언제', '년도', '날짜', '시간', '기간', '며칠']):
        return 'DATE/TIME (시간)'
    elif any(x in text for x in ['어디', '장소', '국가', '도시', '위치', '곳은']):
        return 'LOCATION (장소)'
    elif any(x in text for x in ['몇', '얼마', '개수', '수량']):
        return 'QUANTITY (수량)'
    elif any(x in text for x in ['무엇', '어떤', '무슨', '뜻', '의미']):
        return 'ENTITY/DEFN (사물/개념)'
    else:
        return 'OTHER (기타)'

train_df['q_type'] = train_df['question'].apply(check_question_type)
test_df['q_type'] = test_df['question'].apply(check_question_type)

# 비율 계산
train_type_counts = train_df['q_type'].value_counts(normalize=True).sort_index()
test_type_counts = test_df['q_type'].value_counts(normalize=True).sort_index()

# 시각화
comp_df = pd.DataFrame({'Train': train_type_counts, 'Test': test_type_counts})

plt.figure(figsize=(14, 6))
comp_df.plot(kind='bar', width=0.8, color=['skyblue', 'salmon'])
plt.title("질문 유형별 분포 비교 (NER 전략 수립용)")
plt.ylabel("비율")
plt.xticks(rotation=45)
plt.legend()
plt.tight_layout()
plt.show()

In [ ]:
from collections import Counter

def get_nouns(text_list):
    words = []
    for text in text_list:
        # 간단하게 조사 제거 등을 하지 않고 어절 단위로 카운트 (빠른 확인용)
        # 실제로는 Mecab 등을 쓰는게 좋음
        words.extend(text.split())
    return words

train_words = get_nouns(train_df['question'])
test_words = get_nouns(test_df['question'])

train_counter = Counter(train_words).most_common(20)
test_counter = Counter(test_words).most_common(20)

print("\n=== Train 질문 주요 키워드 ===")
print([w[0] for w in train_counter])

print("\n=== Test 질문 주요 키워드 ===")
print([w[0] for w in test_counter])

In [ ]:
print("\n" + "="*50)
print("🚀 [분석 결론 및 전략 가이드]")
print("="*50)

# 1. 길이 분석 결과에 따른 전략
diff = abs(train_df['q_len'].mean() - test_df['q_len'].mean())
if diff > 5:
    print(f"- 주의: Train과 Test의 질문 길이 차이가 큽니다 ({diff:.2f} tokens).")
    print("  Test 질문이 더 길다면 Retriever 검색 시 쿼리 확장을 고려하세요.")
else:
    print("- 양호: Train과 Test의 질문 길이가 비슷합니다.")

# 2. 질문 유형 분석 결과에 따른 전략 (NER)
top_test_type = test_type_counts.idxmax()
print(f"- Test 데이터에서 가장 많은 질문 유형은 '{top_test_type}' 입니다.")

if 'PERSON' in top_test_type or 'LOCATION' in top_test_type:
    print("  👉 전략: 인물(PER)과 장소(LOC)를 인식하는 NER 모델을 후처리 필터로 반드시 사용하세요.")
    print("  👉 예: 질문에 '누구'가 있으면 답변 후보 중 PER 태그가 없는 것은 감점.")

if 'DATE' in top_test_type or 'QUANTITY' in top_test_type:
    print("  👉 전략: 숫자 정규화(Normalization)와 정규표현식 매칭이 중요합니다.")
    print("  👉 예: '1999년'과 '99년'을 같게 처리하거나, 숫자 답변에 가산점 부여.")

print("="*50)

In [ ]:
with open(os.path.join(data_path, docs_path), "r", encoding="utf-8") as f:
    wiki: dict = json.load(f)
    print(wiki['0'])

In [ ]:
wiki_df = pd.DataFrame.from_dict(wiki, orient='index')

In [ ]:
wiki_df.head(5)

In [ ]:
pd.set_option('display.max_columns', None)

In [ ]:
train_df.head(5)

In [ ]:
test_df.head(5)

In [ ]:
import random

queries_size = len(train_df)

random_indices = random.sample(range(queries_size), 5)
queries = train_df.iloc[random_indices]['question']

In [ ]:
wikis = wiki_df
titles = wikis['title'].tolist()
texts = wikis['text'].tolist()

In [51]:
from rank_bm25 import BM25Okapi
from kiwipiepy import Kiwi

kiwi = Kiwi()

def kiwi_tokenizer(text: str) -> list[str]:
    """
    형태소의 품사가 명사, 동사, 형용사, 숫자, 외국어, 한자 등인 형태소만 추출

    Args:
        text (str): 원본 text

    Returns:
        list[str]: 추출된 형태소 Tokens
    """
    tokens = kiwi.tokenize(text)
    return [
        t.form
        for t in tokens
        if t.tag.startswith("N")
        or t.tag.startswith("V")
        or t.tag.startswith("SN")
        or t.tag.startswith("SL")
        or t.tag.startswith("SH")
    ]

tokenized_corpus = [
    kiwi_tokenizer(tit + " " + txt)
    for tit, txt in zip(titles, texts)
]
bm25 = BM25Okapi(corpus=tokenized_corpus)

In [ ]:
tokenized_corpus

[['나라',
  '목록',
  '문서',
  '나라',
  '목록',
  '이',
  '세계',
  '206',
  '개',
  '나라',
  '현황',
  '주권',
  '승인',
  '정보',
  '개요',
  '형태',
  '나열',
  '있',
  '목록',
  '위하',
  '부분',
  '나뉘',
  '있',
  '번',
  '부분',
  '바티칸 시국',
  '팔레스타인',
  '포함',
  '유엔',
  '등',
  '국제',
  '기구',
  '가입',
  '국제',
  '이',
  '승인',
  '받',
  '여기',
  '195',
  '개',
  '나라',
  '나열',
  '있',
  '번',
  '부분',
  '일부',
  '지역',
  '주권',
  '데',
  '팍토',
  '행사',
  '있',
  '국제',
  '이',
  '승인',
  '받',
  '않',
  '여기',
  '11',
  '개',
  '나라',
  '나열',
  '있',
  '목록',
  '가',
  '나',
  '다',
  '순',
  '이',
  '일부',
  '국가',
  '경우',
  '국가',
  '자격',
  '논쟁',
  '여부',
  '있',
  '때문',
  '목록',
  '엮',
  '것',
  '어렵',
  '논란',
  '생기',
  '수',
  '있',
  '과정',
  '이',
  '목록',
  '구성',
  '있',
  '국가',
  '선정',
  '기준',
  '대하',
  '정보',
  '포함',
  '기준',
  '단락',
  '통하',
  '설명',
  '나라',
  '대하',
  '일반',
  '이',
  '정보',
  '국가',
  '문서',
  '설명',
  '있'],
 ['나라',
  '목록',
  '목록',
  '실리',
  '국가',
  '기준',
  '1933',
  '년',
  '몬테비데오',
  '협약',
  '1',
  '장',
  '참고',
  '하',
  '협정',
  '따르',
  '국가',
  '다음

: 

In [ ]:
from tqdm import tqdm

print("Sparse 검색 중...")
bm25_scores_list = []
bm25_indices_list = []
topk = 10

for query in tqdm(queries, desc="BM25"):
    tokenized_query = kiwi_tokenizer(query)
    scores = bm25.get_scores(tokenized_query)

    # Top-k 인덱스만 뽑아옵니다.
    topk_indices = np.argsort(scores)[::-1][:topk]
    bm25_scores_list.append(scores[topk_indices])
    bm25_indices_list.append(topk_indices)

In [ ]:
bm25_scores_list

In [ ]:
d = {1: 23.3, 2: 21.2, 3:43.1}
sorted(d.items(), key=lambda x: x[1], reverse=True)